# Capstone project: finding right place to place italian restaurant in NYC

### 1. Preparation

In [3]:
# Import required libraries
from bs4 import BeautifulSoup
import requests
import json
import lxml
import pandas as pd
import numpy as np
import folium
import geocoder # import geocoder
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import matplotlib.cm as cm
import matplotlib.colors as colors
import re
import matplotlib.pyplot as plt
import seaborn as sns

In [4]:
CLIENT_ID = 'ZWRMFBTVDUYNIIFCNURVWVABME0CEX0K0YUSAE3ZYYWGMUZQ' # your Foursquare ID
CLIENT_SECRET = 'T0GTHKD1XVSIHYZZBUK452R1ZC45Q2GEKEBA4BIOTR5DK1LC' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

# 2. Load NYC data

In [40]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [2]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [4]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [5]:
neighborhoods_data = newyork_data['features']

In [6]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [7]:
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 
neighborhoods = pd.DataFrame(columns=column_names)

In [8]:
neighborhoods.head()

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [9]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [10]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

### Take a look into all places on map

In [12]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [13]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [14]:
result_frame = pd.DataFrame(columns = ['Borough', 'Neighborhood', 'Venue_name', 'Venue_id', 'Venue_lat', 'Venue_lng'])

In [15]:
result_frame

Empty DataFrame
Columns: [Borough, Neighborhood, Venue_name, Venue_id, Venue_lat, Venue_lng]
Index: []

In [16]:
neighborhoods.head(2)

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939

In [21]:
def get_url(lat, lng):
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId=4bf58dd8d48988d110941735'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    lat, 
    lng, 
    500, 
    50)
    return url

In [ ]:
for ix, row in neighborhoods.iterrows():
    url = get_url(row['Latitude'], row['Longitude'])
    results = requests.get(url).json()
    print(results)
    continue
    venues = results['response']['groups'][0]['items']
    nearby_venues = pd.json_normalize(venues)
    for sub_ix, sub_row in nearby_venues.iterrows():
        sub_frame = pd.DataFrame(data={
                'Borough': [row['Borough']],
                'Neighborhood': [row['Neighborhood']],
                'Venue_name': [sub_row['venue.name']],
                'Venue_id': [sub_row['venue.id']],
                'Venue_lat': [float(sub_row['venue.location.lat'])],
                'Venue_lng':  [float(sub_row['venue.location.lng'])]
        })
        result_frame = result_frame.append(sub_frame)
        

In [ ]:
#result_frame = pd.read_csv('italian_restaurant.csv')

In [ ]:
result_frame.shape

In [ ]:
result_frame.head()

In [ ]:
result_frame.drop_duplicates(subset=['Venue_id'], inplace = True)

In [ ]:
result_frame.head(10)

In [ ]:
result_frame.shape

In [178]:
#result_frame.to_csv('italian_restaurant.csv', index=False)

In [39]:
count_of_places = result_frame.groupby(['Borough', 'Neighborhood'])['Venue_name'].count().reset_index()

In [40]:
joined_count = pd.merge(neighborhoods, count_of_places, on = ['Borough', 'Neighborhood'])

In [ ]:
joined_count.head()

## Let's clear from chain places 

In [186]:
result_frame.Venue_name.value_counts().head(30)

Subway                                        8
Potbelly Sandwich Shop                        7
Patsy's Pizzeria                              5
Rita's Italian Ice & Frozen Custard           5
The Meatball Shop                             5
Olive Garden                                  5
Shorty's                                      4
Parm                                          4
Enzo's                                        3
Italian Pizza                                 3
Lenwich by Lenny's                            3
Sal's Pizzeria                                3
Piccolo Cafe                                  3
Cascarino's                                   3
Bocca Di Bacco                                3
Starbucks                                     3
Farinella Bakery                              2
Via Trenta                                    2
Attraversa                                    2
Sant Ambroeus                                 2
La Grata                                

Okay, we wanna to filter out all places like subway - we're trying to find unique experience

In [187]:
to_drop = ['Subway', 'The Meatball Shop', 'Potbelly Sandwich Shop']

In [188]:
result_frame = result_frame[result_frame['Venue_name'].isin(to_drop) == False]

In [189]:
result_frame.shape

(1649, 6)

In [190]:
result_frame.Venue_name.value_counts().head(30)

Rita's Italian Ice & Frozen Custard              5
Patsy's Pizzeria                                 5
Olive Garden                                     5
Shorty's                                         4
Parm                                             4
Enzo's                                           3
Cascarino's                                      3
Piccolo Cafe                                     3
Italian Pizza                                    3
Starbucks                                        3
Bocca Di Bacco                                   3
Sal's Pizzeria                                   3
Lenwich by Lenny's                               3
Farinella Bakery                                 2
La Pecora Bianca                                 2
Uncle Louie G's Italian Ices and Ice Cream       2
Via Trenta                                       2
Alidoro                                          2
Court Street Grocers                             2
Pasta Wiz                      

In [25]:
result_frame = pd.read_csv('venues_25_all.csv')

In [34]:
result_frame.head()

Borough Neighborhood                Venue_name                  Venue_id  \
0   Bronx    Fieldston       Salvatore's of Soho  4c6994e3c946e21eb28eea8e   
1   Bronx    Fieldston  Caffe Buon Gusto - Bronx  56787589498eca7da2a82944   
2   Bronx    Fieldston          Riverdale Market  4d95272d744f3704e4889a57   
3   Bronx    Riverdale      Bella Notte Pizzeria  55aaee4d498e3cbb70e625d6   
4   Bronx    Riverdale   Mr. Nicks Pizza & Pasta  511b54f17ab47b5a3cc69aec   

   Venue_lat  Venue_lng  
0  40.887633 -73.907178  
1  40.889328 -73.900085  
2  40.891607 -73.897834  
3  40.886595 -73.909556  
4  40.886471 -73.909492

In [36]:
state_geo = f'nyc_neighborhoods.geojson'

In [70]:
joined_count.sort_values(by='Venue_name', ascending=False).head(10)

Borough       Neighborhood   Latitude  Longitude  Venue_name
72  Manhattan          Chinatown  40.715618 -73.994279          72
85  Manhattan            Clinton  40.759101 -73.996119          66
90  Manhattan       East Village  40.727847 -73.982226          58
89  Manhattan  Greenwich Village  40.726933 -73.999914          58
88  Manhattan            Chelsea  40.744035 -74.003116          55
79  Manhattan    Upper East Side  40.775639 -73.960508          53
84  Manhattan     Lincoln Square  40.773529 -73.985338          45
87  Manhattan        Murray Hill  40.748303 -73.978332          43
98  Manhattan  Battery Park City  40.711932 -74.016869          41
86  Manhattan            Midtown  40.754691 -73.981669          40

## Map with colors per amount of restaurants

In [44]:
m = folium.Map(location=[latitude, longitude], zoom_start=11, tiles='cartodbpositron')

In [45]:
m.choropleth(
    geo_data=open(state_geo, encoding='utf-8').read(),
    data=joined_count,
    columns=['Neighborhood', 'Venue_name'],
    key_on='feature.properties.ntaname',
    fill_color='YlGnBu', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='',
    reset=True
)
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='lightblue',
        fill=True,
        fill_opacity=0.7,
        parse_html=False).add_to(m)  
    

In [46]:
m

In [191]:
result_frame.to_csv('venues_25_all.csv', index=False)

In [3]:
result_frame = pd.read_csv('venues_25_all.csv')

In [4]:
result_frame = result_frame.reset_index().drop(columns=['index'])

In [5]:
result_frame.shape

(1649, 6)

In [6]:
result_frame_part_1 = result_frame.loc[0:450]

In [7]:
result_frame_part_2 = result_frame.loc[450:900]

In [8]:
result_frame_part_3 = result_frame.loc[900:1350]

In [9]:
result_frame_part_4 = result_frame.loc[1350:]

In [10]:
result_frame_part_1.shape

(451, 6)

In [11]:
result_frame_part_2.shape

(451, 6)

In [12]:
result_frame_part_3.shape

(451, 6)

In [13]:
result_frame_part_4.shape

(299, 6)

In [3]:
result_frame_part_1.to_csv('venues_part_1.csv', index=False)

NameError: name 'result_frame_part_1' is not defined

In [3]:
result_frame_part_1 = pd.read_csv('venues_part_1.csv')

In [ ]:
result_frame_part_2.to_csv('venues_part_2.csv', index=False)

In [4]:
result_frame_part_2 = pd.read_csv('venues_part_2.csv')

In [5]:
result_frame_part_3.to_csv('venues_part_3.csv', index=False)

NameError: name 'result_frame_part_3' is not defined

In [5]:
result_frame_part_3 = pd.read_csv('venues_part_3.csv')

In [17]:
result_frame_part_4.to_csv('venues_part_4.csv', index=False)

In [6]:
result_frame_part_4 = pd.read_csv('venues_part_4.csv')

In [7]:
result_frame_part_1.head()

Borough Neighborhood                Venue_name                  Venue_id  \
0   Bronx    Fieldston       Salvatore's of Soho  4c6994e3c946e21eb28eea8e   
1   Bronx    Fieldston  Caffe Buon Gusto - Bronx  56787589498eca7da2a82944   
2   Bronx    Fieldston          Riverdale Market  4d95272d744f3704e4889a57   
3   Bronx    Riverdale      Bella Notte Pizzeria  55aaee4d498e3cbb70e625d6   
4   Bronx    Riverdale   Mr. Nicks Pizza & Pasta  511b54f17ab47b5a3cc69aec   

   Venue_lat  Venue_lng  
0  40.887633 -73.907178  
1  40.889328 -73.900085  
2  40.891607 -73.897834  
3  40.886595 -73.909556  
4  40.886471 -73.909492

In [8]:
result_frame_part_2.head()

Borough       Neighborhood          Venue_name                  Venue_id  \
0  Brooklyn         Georgetown  Vikki's Restaurant  4d15240925cda143617c67d6   
1  Brooklyn  East Williamsburg       Ammazza Caffe  58eac71c0319b80a65d5045b   
2  Brooklyn  East Williamsburg        Il Passatore  4a358dfaf964a5202d9d1fe3   
3  Brooklyn  East Williamsburg     Roberta's Pizza  47e100b9f964a520414e1fe3   
4  Brooklyn  East Williamsburg    Lella Alimentari  56055323498e16b73108b749   

   Venue_lat  Venue_lng  
0  40.619381 -73.917465  
1  40.711543 -73.944574  
2  40.714463 -73.941956  
3  40.705015 -73.933617  
4  40.715133 -73.946342

In [9]:
result_frame_part_3.head()

Borough Neighborhood          Venue_name                  Venue_id  \
0  Manhattan      Chelsea      Bocca Di Bacco  50d0ff3be4b0faa0056674db   
1  Manhattan      Chelsea          Intermezzo  49c9b04ff964a52091581fe3   
2  Manhattan      Chelsea              Pastai  51437e02e4b080a1097d4a95   
3  Manhattan      Chelsea              Filaga  56fff9b4498e1acc6cfc46a7   
4  Manhattan      Chelsea  Chelsea Ristorante  4a7e16e3f964a520eaf01fe3   

   Venue_lat  Venue_lng  
0  40.744561 -74.002813  
1  40.743596 -73.999699  
2  40.745390 -74.001826  
3  40.741975 -74.005623  
4  40.740739 -74.001910

In [10]:
result_frame_part_4.head()

Borough     Neighborhood                       Venue_name  \
0  Queens  Jackson Heights  Sal's Bar Restaurant & Pizzeria   
1  Queens  Jackson Heights          JC Italian Delicatessen   
2  Queens  Jackson Heights                    Italian Farms   
3  Queens         Elmhurst             Little Caesars Pizza   
4  Queens         Elmhurst                       Limoncello   

                   Venue_id  Venue_lat  Venue_lng  
0  4f04aa23e4b04fbec49ff81d  40.755595 -73.886248  
1  51607c96e4b00021037808ff  40.749603 -73.884531  
2  4b23e7a3f964a520835c24e3  40.749763 -73.884531  
3  52f543e211d242eeca9b4438  40.748052 -73.879693  
4  4d951fcd0caaa143774157b3  40.746486 -73.883377

## API gathering function

In [11]:
def get_stats_for_venues(df: pd.DataFrame):
    df['PriceTier'] = 0
    df['LikesCount'] = 0
    df['Dislike'] = 0
    df['Rating'] = 0
    df['BeenHereCount'] = 0
    df['PhotosCount'] = 0
    df['ReasonsCount'] = 0
    df['TipsCount'] = 0
    for ix, row in df.iterrows():
        venue_url = f'https://api.foursquare.com/v2/venues/{row["Venue_id"]}?&client_id={CLIENT_ID}&client_secret={CLIENT_SECRET}&v={VERSION}'
        #print(venue_url)
        results = requests.get(venue_url).json()
        #venue = results['response']
        #result_venue = pd.json_normalize(venue)
        df.loc[ix, 'PriceTier'] = results['response']['venue']['price'].get('tier', 0) if results['response']['venue'].get('price', -1) != -1 else 0
        df.loc[ix, 'LikesCount'] = results['response']['venue']['likes'].get('count', 0) if results['response']['venue'].get('likes', -1) != -1 else 0
        df.loc[ix, 'Dislike'] = results['response']['venue'].get('dislike', 0)
        df.loc[ix, 'Rating'] = results['response']['venue'].get('rating', 0)
        df.loc[ix, 'BeenHereCount'] = results['response']['venue']['beenHere'].get('count', 0) if results['response']['venue'].get('beenHere', -1) != -1 else 0
        df.loc[ix, 'PhotosCount'] = results['response']['venue']['photos'].get('count', 0) if results['response']['venue'].get('photos', -1) != -1 else 0
        df.loc[ix, 'ReasonsCount'] = results['response']['venue']['reasons'].get('count', 0) if results['response']['venue'].get('reasons', -1) != -1 else 0
        df.loc[ix, 'TipsCount'] = results['response']['venue']['tips'].get('count', 0) if results['response']['venue'].get('tips', -1) != -1 else 0
    return df

## Process one dataset

In [12]:
part_4_result = get_stats_for_venues(result_frame_part_4)

In [13]:
part_4_result

Borough     Neighborhood                           Venue_name  \
0           Queens  Jackson Heights      Sal's Bar Restaurant & Pizzeria   
1           Queens  Jackson Heights              JC Italian Delicatessen   
2           Queens  Jackson Heights                        Italian Farms   
3           Queens         Elmhurst                 Little Caesars Pizza   
4           Queens         Elmhurst                           Limoncello   
..             ...              ...                                  ...   
294  Staten Island     Prince's Bay                             Fratelli   
295  Staten Island     Prince's Bay       Ralph's Italian Ices- Huguenot   
296       Brooklyn          Madison                            Michael's   
297          Bronx        Bronxdale  Tina's italian bakery & pastry shop   
298      Manhattan     Hudson Yards                       Skylight Diner   

                     Venue_id  Venue_lat  Venue_lng  PriceTier  LikesCount  \
0    4f04aa23e4b04fbec49ff81d  40.755595 -73.886248          2           0   
1    51607c96e4b00021037808ff  40.749603 -73.884531          1           0   
2    4b23e7a3f964a520835c24e3  40.749763 -73.884531          0           2   
3    52f543e211d242eeca9b4438  40.748052 -73.879693          1           6   
4    4d951fcd0caaa143774157b3  40.746486 -73.883377          2           2   
..                        ...        ...        ...        ...         ...   
294  4e4ce95ebd413c4cc66d2a8f  40.525690 -74.200630          2           1   
295  4f7f443fe4b0ac821d838d4f  40.528343 -74.198629          1           0   
296  42508380f964a520c1201fe3  40.607520 -73.943044          3          57   
297  4bae4b3ef964a520a29e3be3  40.854202 -73.860850          1           0   
298  3fd66200f964a520b4e31ee3  40.753379 -73.996792          2         244   

    Dislike  Rating  BeenHereCount  PhotosCount  ReasonsCount  TipsCount  
0     False     0.0              0            5             0          1  
1     False     0.0              0            1             0          1  
2     False     0.0              0            0             0          4  
3     False     7.0              0           18             0          6  
4     False     0.0              0           13             0          3  
..      ...     ...            ...          ...           ...        ...  
294   False     0.0              0            0             0          0  
295   False     0.0              0            0             0          0  
296   False     8.1              0           70             1         11  
297   False     0.0              0            0             0          0  
298   False     6.4              0          256             1        109  

[299 rows x 14 columns]

In [14]:
part_4_result.to_csv('part_4_results_v2.csv', index=False)

## Load all previously prepared results

In [12]:
part_1_results = pd.read_csv('part_1_results_v2.csv')

In [21]:
part_2_results = pd.read_csv('part_2_results_v2.csv')

In [23]:
part_3_results = pd.read_csv('part_3_results_v2.csv')

In [25]:
part_4_results = pd.read_csv('part_4_results_v2.csv')

In [ ]:
results_dataset = pd.concat([part_1_results, part_2_results, part_3_results, part_4_result])

In [ ]:
results_dataset.head()

In [ ]:
results_dataset.shape

## And save it to one file, as dataset for next notebook

In [22]:
results_dataset.to_csv('final_results.csv', index = False)